# Robot Setup Code

Imports the necessary class libraries and creates our *postman* robot instance.  
This is at the top of our notebook because it must be run before any of the other notebook cells.  

In [1]:
from easygopigo3 import EasyGoPiGo3
import numpy as np
import time
import threading

# create a robot instance and call it courier
courier = EasyGoPiGo3()


# Interactivity Setup Code

Imports the necessary class libraries and creates our *courier* robot instance.  
This is at the top of our notebook because it must be run before any of the other notebook cells.  

In [2]:
from  ipywidgets import widgets, Layout, Output, VBox, HBox
from IPython.display import display
import matplotlib.pyplot as plt
%matplotlib inline
#%matplotlib ipympl

output = Output()

# Sensor Setup Code

Tell the GoPiGo3 which port you have plugged the ** *light and color* ** and ** *line follower* ** sensors into and initialize them  

(see the LEARN section of the mission document for more details)

# Variable Container Class

A container within which we can declare and initialize all our global variables.  
An instance of this container class should be created in the **Variable Initialization** cell.  

(see the LEARN section of the mission document for more details)

In [3]:
class GlobalVariables():
    
    # attributes set by color sensor template functions
    color_sensor_reading = [0,0,0,0]
    color_name           = None
    
    # attributes set by realtime_data_analysis template function
    red_values           = []
    green_values         = []
    blue_values          = []
    clear_values         = []    
    reading_times        = []
    start_time           = time.time()

    #attribute  set by Read Address button
    address_color        = None    

    # attribute set by Emergency Stop button
    emergency_stop_flag  = 0
    
    def __init__(self):
        print ("creating a variable container class...")

# Variable Initialization

Instantiation of the variable container class  
The *init()* function must be called at the start of the **Interactive Control Code** cell to re-initialize everything.  

(see the LEARN section of the mission document for more details)

In [4]:
def init():
    print("initializing variables...")

# Line Follower Template Functions

Template functions for working with the line sensor, borrowed directly from the **Warehouse Stock Picker** mission.  

(for more information, please read the **Warehouse Stock Picker** mission)

In [5]:
def elapsed_time():
    global var
    return time.time() - var.start_time

def calibrate_line_follower():
 
    line_follower.set_calibration('black')
    values = line_follower.black_calibration
    print(f"BLACK: AVERAGE = {np.mean(values):.2f} \t MINIMUM = {np.amin(values):.2f} \t MAXIMUM = {np.amax(values):.2f}")

    courier.drive_cm(5)

    line_follower.set_calibration('white')
    values = line_follower.white_calibration
    print(f"WHITE: AVERAGE = {np.mean(values):.2f} \t MINIMUM = {np.amin(values):.2f} \t MAXIMUM = {np.amax(values):.2f}")

    


# Template Functions

**read_color_sensor()**

Takes a reading from the light & color sensor and records a timestamp (elapsed time) for this reading.  
Appends individual color values to the <color> value lists (for graph drawing purposes)

You should declare and initialize a *start_time* variable in the **Variable Initialization** cell.

**record_color(eye)**

Illuminate the specified eye(s) the same color as the last color read  
**eye**: which eye(s) to illuminate (one of 'left' / 'right' / 'both')

In [6]:
def read_color_sensor():
    global var
    
    # read the sensor
    # color_sensor_reading = [red, green, blue, clear]
    var.color_sensor_reading = color_sensor.safe_raw_colors()
    
    # obtain a timestamp for our reading - add this to the list of reading times
    var.reading_times.append(elapsed_time())
    
    # add the latest values to the end of our data lists
    var.red_values.append(var.color_sensor_reading[0])
    var.green_values.append(var.color_sensor_reading[1])
    var.blue_values.append(var.color_sensor_reading[2])
    var.clear_values.append(var.color_sensor_reading[3])
    

def record_color(eye):
    global var

    var.color_name, color_rgb_values = color_sensor.guess_color_hsv(var.color_sensor_reading)
    
    if eye == 'both':
        courier.set_eye_color(color_rgb_values)
    elif eye == 'left':
        courier.set_left_eye_color(color_rgb_values)
    elif eye == 'right':
        courier.set_right_eye_color(color_rgb_values)
    else:
        print (f"ERROR: invalid eye {eye}")
        
    courier.open_eyes()

# Main Code

Your mission code goes in here

# Interactive Control Code

**read_delivery_address()**

Place a colour-coded card under the robot's color sensor and run this function to register the "address" to deliver the card to 


In [ ]:
def test_line(_):
    output.clear_output()
    with output:
        test_line_follower()
        
def test_color(_):
    output.clear_output()
    with output:
        test_color_sensor()
                
def calibrate_line(_):
    output.clear_output()
    with output:
        calibrate_line_follower()
        
def calibrate_color(_):    
    output.clear_output()
    with output:
        colors = ['yellow','fuchsia','red','green','blue','black','white']
        for i in range(len(colors)):
            read_color_sensor()
            record_color('left')
            time.sleep(1)
            color_sensor.calibrate(colors[i])
            read_color_sensor()
            record_color('right')
            time.sleep(1)
            courier.drive_cm(4.5)
        for i in range (0,3):
            courier.close_eyes()
            time.sleep(0.5)
            courier.open_eyes()
            time.sleep(0.5)
        courier.close_eyes()

def start_data_analysis(_):
    output.clear_output()
    with output:
        thread = threading.Thread(target=realtime_data_analysis)
        thread.start()

def stop_data_analysis(_):
    global var
    var.emergency_stop_flag = 1

def read_delivery_address(_):
    output.clear_output()
    with output:
        print ("Reading your address...")
        
        # WRITE YOUR CHALLENGE CODE HERE 

def deliver(_):
    global var
    output.clear_output()
    with output:
        print (f"Thank you for your custom. Delivering your card to the {var.address_color} house.")
        thread = threading.Thread(target=main)
        thread.start()
        
def emergency_stop(_):
    global var
    output.clear_output()
    with output:       
        print (f"Houston, we have a problem!")
        var.emergency_stop_flag = 1
        courier.stop()
        courier.close_eyes()
        
init()

items_layout = Layout(flex='1 1 auto', width='auto')
box_layout = Layout(display='flex', flex_flow='column', align_items='stretch', border='solid', width='600px')

# set up the display for the graph
handle = display(None, display_id=True)

buttons = []

buttons.append(widgets.Button(description="Test Line Follower", layout=items_layout))
buttons.append(widgets.Button(description="Test Color Sensor", layout=items_layout))
buttons.append(widgets.Button(description="Calibrate Line Follower", layout=items_layout))
buttons.append(widgets.Button(description="Calibrate Color Sensor", layout=items_layout))
buttons.append(widgets.Button(description="Start Data Analysis", layout=items_layout))
buttons.append(widgets.Button(description="Stop Data Analysis", layout=items_layout))
buttons.append(widgets.Button(description="Read Address", layout=items_layout))
buttons.append(widgets.Button(description="Deliver Letter", layout=items_layout))
buttons.append(widgets.Button(description="Emergency Stop", layout=items_layout))

buttons[0].on_click(test_line)
buttons[1].on_click(test_color)
buttons[2].on_click(calibrate_line)
buttons[3].on_click(calibrate_color)
buttons[4].on_click(start_data_analysis)
buttons[5].on_click(stop_data_analysis)
buttons[6].on_click(read_delivery_address)
buttons[7].on_click(deliver)
buttons[8].on_click(emergency_stop)

row1 = HBox( [buttons[0], buttons[1]] )
row2 = HBox( [buttons[2], buttons[3]] )
row3 = HBox( [buttons[4], buttons[5]] )
row4 = HBox( [buttons[6], buttons[7]] )
row5 = HBox( [buttons[8]] )

VBox( [row1, row2, row3, row4, row5, output], layout=box_layout )

# Data Analysis Code

Displays a continuously updating plot of RGB & clear values read from the color sensor.  
The functions in this cell are run when the *Start Data Analysis* button is clicked on in the control panel.

In [9]:
def update_graph(graph):
    
    global var
        
    graph.clear()
    
    graph.plot(var.reading_times[-10:], var.red_values[-10:], 'r-', label="red value")
    graph.plot(var.reading_times[-10:], var.green_values[-10:], 'g-', label="green value")
    graph.plot(var.reading_times[-10:], var.blue_values[-10:], 'b-', label="blue value")
    graph.plot(var.reading_times[-10:], var.clear_values[-10:], 'k--', label="clear value")
    
    graph.set_title('Color Sensor Readings')
    graph.set_xlabel('reading time    (seconds)')
    graph.set_ylabel('reading value    (min = 0, max = 1)')
    graph.legend(bbox_to_anchor=(1.35, 1), loc=1)
    
def realtime_data_analysis():
    
    global var
    var.emergency_stop_flag = 0

    # set up the figure and plot
    fig = plt.figure()
    graph = fig.add_subplot(111)
    
    # turn the "interactive" mode ON
    plt.ion()

    while var.emergency_stop_flag == 0:
        
        read_color_sensor()
        record_color('both')

        update_graph(graph)
        handle.update(fig)
        
        time.sleep(0.05)